In [9]:
import json
import psycopg2
from datetime import datetime
import time
import pandas as pd

In [2]:
def connect_to_postgres_database(db_name):
    try:
        conn = psycopg2.connect(
            dbname=db_name, 
            user='postgres', 
            password='king', 
            host='localhost'
        )
        conn.autocommit = True
        cursor = conn.cursor()
        print(f"Connected to PostgreSQL db {db_name}")
        return conn, cursor
    except Exception as e:
        print("An error occurred while connecting: ", e)

In [96]:
def create_database(cursor, db_name):
    try:
        cursor.execute(f'CREATE DATABASE "{db_name}"')
        print(f"Database {db_name} created successfully")
    except Exception as e:
        print("An error occurred while creating the database: ", e)

In [7]:
def create_table(cursor):
    try:
        cursor.execute("""
            CREATE TABLE IF NOT EXISTS users (
                id VARCHAR(255) PRIMARY KEY,
                name VARCHAR(255),
                screen_name VARCHAR(255),
                verified BOOLEAN,
                location VARCHAR(255),
                description VARCHAR(255),
                followers_count BIGINT,
                friends_count BIGINT, 
                favourites_count BIGINT,
                statuses_count BIGINT,
                tweets_count BIGINT,
                created_at TIMESTAMP
            )
            """)
        conn.commit()
        print("Table 'users' created successfully")
    except Exception as e:
        print("An error occurred while creating the table: ", e)

In [98]:
conn, cursor = connect_to_postgres_database('postgres')

Connected to PostgreSQL db postgres


In [99]:
create_database(cursor, 'twitter-database')
conn.close()

Database twitter-database created successfully


In [21]:
# Close the previous connection and connect to the new database
conn, cursor = connect_to_postgres_database('twitter-database')

Connected to PostgreSQL db twitter-database


In [6]:
create_table(cursor)

Table 'users' created successfully


In [10]:
df = pd.read_csv("../data/tweets_counts.csv")

In [30]:
import numpy
from psycopg2.extensions import register_adapter, AsIs
def addapt_numpy_float64(numpy_float64):
    return AsIs(numpy_float64)
def addapt_numpy_int64(numpy_int64):
    return AsIs(numpy_int64)
register_adapter(numpy.float64, addapt_numpy_float64)
register_adapter(numpy.int64, addapt_numpy_int64)

In [31]:
class User(object):
    
    def __init__(self, user):
        self.id = user['id_str']
        self.name = user['name']
        self.screen_name = user['screen_name']
        self.verified = user['verified']
        self.location = user['location']
        self.description = user['description']
        self.followers_count = user['followers_count']
        self.friends_count = user['friends_count']
        self.favourites_count = user['favourites_count']
        self.statuses_count = user['statuses_count']
        self.tweets_count = user['tweets_count']
        self.created_at = self.get_created_date(user['created_at'])
    
    @staticmethod    
    def get_created_date(created_at):
        created_at_date = datetime.strptime(created_at, "%a %b %d %H:%M:%S %z %Y")
        created_at_date = created_at_date.strftime("%Y-%m-%d %H:%M:%S")
        return created_at_date
        
    def get_user(self):
        return (self.id, self.name, self.screen_name, self.verified, self.location, self.description,
                self.followers_count, self.friends_count, self.favourites_count, self.statuses_count, self.tweets_count, self.created_at)
    
    

In [32]:
def insert_user(cursor, user):
    try:
        cursor.execute("""
            INSERT INTO users (id, name, screen_name, verified, location, description, followers_count, friends_count, favourites_count, statuses_count, tweets_count, created_at)
            VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
        """, user)
        conn.commit()
        print("User inserted into table successfully")
    except Exception as e:
        print("An error occurred while inserting data: ", e)

In [33]:
def load_unique_user(db_cursor, user, users):
    if user['id_str'] not in users:
        filtered_df = df[df['User_ID'] == int(user['id_str'])]
        if not filtered_df.empty:
            tweet_count = filtered_df.iloc[0]['Tweets_Count']
        else:
            tweet_count = 0
        user['tweets_count'] = tweet_count
        users.add(user['id_str'])
        user_object = User(user)
        insert_user(db_cursor, user_object.get_user())
        print(f"Inserted users: {len(users)}")      

In [34]:
def load_user_data_to_database(db_cursor, file_path, users):
    
    start_time = time.time()
    
    with open(file_path, "r") as file:
        for line in file:
            try:
                data = json.loads(line)
                
                user = data['user']
                load_unique_user(db_cursor, user, users)
                
                if data.get('retweeted_status'):
                    retweeted_user = data.get('retweeted_status').get('user')
                    load_unique_user(db_cursor, retweeted_user, users)
                    
                if data.get('quoted_status'):
                    quoted_user = data.get('quoted_status').get('user')
                    load_unique_user(db_cursor, quoted_user, users)                   
            except:
                continue
    
    print(f"Successfully inserted {len(users)} users in {time.time() - start_time} seconds")

In [35]:
users = set()

In [36]:
load_user_data_to_database(cursor, "../data/corona-out-2", users)

User inserted into table successfully
Inserted users: 1
User inserted into table successfully
Inserted users: 2
User inserted into table successfully
Inserted users: 3
User inserted into table successfully
Inserted users: 4
User inserted into table successfully
Inserted users: 5
User inserted into table successfully
Inserted users: 6
User inserted into table successfully
Inserted users: 7
User inserted into table successfully
Inserted users: 8
User inserted into table successfully
Inserted users: 9
User inserted into table successfully
Inserted users: 10
User inserted into table successfully
Inserted users: 11
User inserted into table successfully
Inserted users: 12
User inserted into table successfully
Inserted users: 13
User inserted into table successfully
Inserted users: 14
User inserted into table successfully
Inserted users: 15
User inserted into table successfully
Inserted users: 16
User inserted into table successfully
Inserted users: 17
User inserted into table successfully
In

In [37]:
load_user_data_to_database(cursor, "../data/corona-out-3", users)

User inserted into table successfully
Inserted users: 19233
User inserted into table successfully
Inserted users: 19234
User inserted into table successfully
Inserted users: 19235
User inserted into table successfully
Inserted users: 19236
User inserted into table successfully
Inserted users: 19237
User inserted into table successfully
Inserted users: 19238
User inserted into table successfully
Inserted users: 19239
User inserted into table successfully
Inserted users: 19240
User inserted into table successfully
Inserted users: 19241
User inserted into table successfully
Inserted users: 19242
User inserted into table successfully
Inserted users: 19243
User inserted into table successfully
Inserted users: 19244
User inserted into table successfully
Inserted users: 19245
User inserted into table successfully
Inserted users: 19246
User inserted into table successfully
Inserted users: 19247
User inserted into table successfully
Inserted users: 19248
User inserted into table successfully
In